## **Автоматическое распознавание номерных знаков**

### **1. Разметка**

#### 1.1 Соберем необходимые данные

`Для построения модели распознавания номерных знаков, нам нужны данные. Для этого нам нужно собрать как можно больше изображений транспортных средств, на которых изображен номерной знак. Стандартные датасеты не совсем подходили для этой задачи, т.к. на них транспортные средства изображены в чистом виде и номерные знаки отчетливо видны. На практике, такие ситуации очень редкое явление, номерные знаки скорее изображены под разными углами и на них присутствует зашумление изображения. Вот пример данных, который я использовал для этого проекта. Ниже представлены несколько примеров.

<img src="image/image_1.jpg" width="300" height="200">
        
<img src="image/image_2.jpg" width="300" height="200">  

<img src="image/image_3.jpg" width="300" height="200"> 

<img src="image/image_4.jpg" width="300" height="200"> 

#### 1.2 Метки изображений

Для разметки изображений я использовал LabelImg. Загрузите labelImg с [GitHub](https://github.com/HumanSignal/labelImg/tree/master) и следуйте инструкциям по установке пакета. После этого откройте GUI, как указано в инструкции, нажмите CreateRectBox и нарисуйте прямоугольный блок, как показано ниже, и сохраните вывод в XML.

<img src="image\image_5.png" width="800" height="400">


#### 1.3 Парсинг информации из XML
Пример файла XML представлен ниже

``` xml
<annotation>
    <folder>images</folder>
    <filename>N1.jpeg</filename>
    <path>/Users/asik/Desktop/ANPR/imagesN1.jpeg</path>
    <source>
        <database>Unknown</database>
    </source>
    <size>
        <width>1920</width>
        <height>1080</height>
        <depth>3</depth>
    </size>
    <segmented>0</segmented>
    <object>
        <name>number_plate</name>
        <pose>Unspecified</pose>
        <truncated>0</truncated>
        <difficult>0</difficult>
        <bndbox>
            <xmin>1093</xmin>
            <ymin>645</ymin>
            <xmax>1396</xmax>
            <ymax>727</ymax>
        </bndbox>
    </object>
</annotation>

Затем выполняем предварительную обработку данных. Поскольку вывод метки — это XML, для того, чтобы использовать это для процесса обучения, нам нужны данные в формате массива. Для этого мы возьмем полезную информацию из метки, которая является диагональными точками прямоугольного поля или ограничивающего поля, которые равны xmin, ymin, xmax, ymax соответственно. Извлекаем полученную информацию и сохраняем ее в формате CSV. 

#### 1.4 Анализ данных XML и преобразование в CSV

In [ ]:
# загрузим библиотеки
import os
import cv2
import numpy as np
import pandas as pd
import tensorflow as tf
import pytesseract as pt
import plotly.express as px
import matplotlib.pyplot as plt
import xml.etree.ElementTree as xet
import nbformat

from glob import glob
from skimage import io
from shutil import copy
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import TensorBoard
from sklearn.model_selection import train_test_split
from tensorflow.keras.applications import InceptionResNetV2
from tensorflow.keras.layers import Dense, Dropout, Flatten, Input
from tensorflow.keras.preprocessing.image import load_img, img_to_array

In [19]:
path = glob('./images/*.xml')
labels_dict = dict(filepath=[],xmin=[],xmax=[],ymin=[],ymax=[])
for filename in path:

    info = xet.parse(filename)
    root = info.getroot()
    member_object = root.find('object')
    labels_info = member_object.find('bndbox')
    xmin = int(labels_info.find('xmin').text)
    xmax = int(labels_info.find('xmax').text)
    ymin = int(labels_info.find('ymin').text)
    ymax = int(labels_info.find('ymax').text)

    labels_dict['filepath'].append(filename)
    labels_dict['xmin'].append(xmin)
    labels_dict['xmax'].append(xmax)
    labels_dict['ymin'].append(ymin)
    labels_dict['ymax'].append(ymax)

В приведенном выше коде мы по отдельности берем каждый файл и анализируем в xml.etree и находим объект -> bndbox. Затем мы извлекаем xmin,xmax,ymin,ymax и сохраняем эти значения в словаре. После этого мы преобразуем его в фрейм данных pandas и сохраняем его в файл CSV и сохраняем его в папке проекта, как показано ниже.

In [20]:
# Извлекаем bndbox и сохраняем его в словаре
df = pd.DataFrame(labels_dict)
df.to_csv('labels.csv',index=False)
df.head()

filepath  xmin  xmax  ymin  ymax
0     ./images\N1.xml   338   514   300   340
1    ./images\N10.xml   231   436   446   501
2   ./images\N100.xml   232   342   278   323
3  ./images\N1000.xml    95   190   170   206
4  ./images\N1001.xml   118   223   238   287

С помощью приведенного выше кода мы извлекаем диагональное положение каждого изображения и преобразуем данные из неструктурированного в структурированный формат. Вы можете посмотреть данные выше. Теперь также извлеките соответствующее имя файла изображения XML.

In [21]:
filename = df['filepath'][0]
def getFilename(filename):
    filename_image = xet.parse(filename).getroot().find('filename').text
    filepath_image = os.path.join('./images',filename_image)
    return filepath_image
getFilename(filename)

'./images\\N1.jpeg'

In [22]:
image_path = list(df['filepath'].apply(getFilename))
image_path[:10]#random check

['./images\\N1.jpeg',
 './images\\N10.jpeg',
 './images\\N100.jpeg',
 './images\\N1000.jpeg',
 './images\\N1001.jpeg',
 './images\\N1002.jpeg',
 './images\\N1003.jpeg',
 './images\\N1004.jpeg',
 './images\\N1005.jpeg',
 './images\\N1006.jpeg']

#### 1.5 Проверим данные

In [ ]:
# Посмотрим правильность извлеченного bndbox и изображения
# Данные подставляются вручную
file_path = image_path[4] # image №4 из датасета

# читаем изображение
img = cv2.imread(file_path) 
# xmin-1804/ymin-1734/xmax-2493/ymax-1882 
img = io.imread(file_path)
fig = px.imshow(img)

# разметку проставляю вручную из датасета, т.е. смотрим в датасет строка 4 и заполняем данные
fig.update_layout(width=640, height=480, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='image N1001.jpeg with bounding box') 
fig.add_shape(type='rect',x0=118, x1=223, y0=238, y1=287, xref='x', yref='y',line_color='cyan')

Как видим выше, разметка и изображение успешно извлечены.

### **2. Обработка данных**

#### 2.1 Чтение данных

На этом шаге мы возьмем каждое изображение и преобразуем его в массив с помощью OpenCV, а затем изменим размер изображения до 224 x 224, что является стандартным совместимым размером предварительно обученной модели.

In [ ]:
labels = df.iloc[:,1:].values
data = []
output = []

for ind in range(len(image_path)):
    image = image_path[ind]
    img_arr = cv2.imread(image)
    
    # Проверка, что изображение успешно загружено
    # на этом шаге проверяем корректность загруженных изображений, изображения которые некорректно загружены я просто удалил.
    if img_arr is None:
        print(f"Ошибка: Не удалось загрузить изображение {image}")
        continue  # Пропустить это изображение и перейти к следующему
    
    h, w, d = img_arr.shape
    
    # Предварительная обработка
    load_image = load_img(image, target_size=(224, 224))
    load_image_arr = img_to_array(load_image)
    norm_load_image_arr = load_image_arr / 255.0  # Normalization
    
    # Нормализация меток
    xmin, xmax, ymin, ymax = labels[ind]
    nxmin, nxmax = xmin / w, xmax / w
    nymin, nymax = ymin / h, ymax / h
    label_norm = (nxmin, nxmax, nymin, nymax)  # Normalized output
    
    # Append
    data.append(norm_load_image_arr)
    output.append(label_norm)

# Преобразуем списки в массивы NumPy для дальнейшего использования
data = np.array(data)
output = np.array(output)

После этого мы нормализуем изображение, просто разделив его на максимальное число, поскольку мы знаем, что максимальное число для 8-битного изображения равно 28 -1 = 255. Вот почему мы разделим наше изображение на 255,0. Способ деления массива на максимальное значение называется нормализацией (масштабирование минимума и максимума). Нам также нужно нормализовать наши метки. Потому что для модели глубокого обучения выходной диапазон должен быть от 0 до 1. Для нормализации меток нам нужно разделить диагональные точки на ширину и высоту изображения. И, наконец, значения в списке Python.

#### 3.2 Разделение данных на train и  test

Преобразуем данные в массив numpy

In [24]:
# Convert data to array
X = np.array(data,dtype=np.float32)
y = np.array(output,dtype=np.float32)

Теперь разделим данные на обучающий и тестовый наборы с помощью sklearn.

In [25]:
# Split the data into training and testing set using sklearn.
x_train,x_test,y_train,y_test = train_test_split(X,y,train_size=0.8,random_state=0)
x_train.shape,x_test.shape,y_train.shape,y_test.shape

((879, 224, 224, 3), (220, 224, 224, 3), (879, 4), (220, 4))

### 3. Deep Learning для обнаружения объектов

#### 3.1. Построение Inception-ResNet-v2

Inception-ResNet-v2 — это сверточная нейронная сеть, обученная на более чем миллионе изображений из базы данных ImageNet. Сеть имеет глубину 164 слоя и может классифицировать изображения по 1000 категориям объектов, таким как клавиатура, мышь, карандаш и многие животные. В результате сеть выучила богатые представления признаков для широкого спектра изображений. Inception-ResNet-v2 использовалась для задачи классификации. Архитектура сети показана на рисунке ниже. Inception-Resnet-v2 сформулирована на основе комбинации структуры Inception и остаточного соединения. В блоке Inception-Resnet сверточные фильтры нескольких размеров объединяются остаточными соединениями. Использование обратных соединений не только позволяет избежать проблемы деградации, вызванной глубокими структурами, но и сокращает время обучения.

<img src="image\Notebook7.png" width="300" height="500">

Мы готовы обучить модель глубокого обучения для обнаружения объектов. Здесь мы будем использовать модель Inception-ResNet-v2 с предварительно обученными весами и обучим ее на наших данных. Мы уже импортировали необходимые библиотеки из TensorFlow ранее

In [26]:
inception_resnet = InceptionResNetV2(weights="imagenet",include_top=False, input_tensor=Input(shape=(224,224,3)))
# ---------------------
headmodel = inception_resnet.output
headmodel = Flatten()(headmodel)
headmodel = Dense(500,activation="relu")(headmodel)
headmodel = Dense(250,activation="relu")(headmodel)
headmodel = Dense(4,activation='sigmoid')(headmodel)


# ---------- model
model = Model(inputs=inception_resnet.input,outputs=headmodel)

In [27]:
# Complie model
model.compile(loss='mse',optimizer=tf.keras.optimizers.Adam(learning_rate=1e-4))
model.summary()

Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 224, 224,  │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d (Conv2D)     │ (None, 111, 111,  │        864 │ input_layer[0][0] │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalization │ (None, 111, 111,  │         96 │ conv2d[0][0]      │
│ (BatchNormalizatio… │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation          │ (None, 111, 111,  │          0 │ batch_normalizat… │
│ (Activation)        │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_1 (Conv2D)   │ (None, 109, 109,  │      9,216 │ activation[0][0]  │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 109, 109,  │         96 │ conv2d_1[0][0]    │
│ (BatchNormalizatio… │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_1        │ (None, 109, 109,  │          0 │ batch_normalizat… │
│ (Activation)        │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 109, 109,  │     18,432 │ activation_1[0][… │
│                     │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 109, 109,  │        192 │ conv2d_2[0][0]    │
│ (BatchNormalizatio… │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_2        │ (None, 109, 109,  │          0 │ batch_normalizat… │
│ (Activation)        │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ max_pooling2d       │ (None, 54, 54,    │          0 │ activation_2[0][… │
│ (MaxPooling2D)      │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_3 (Conv2D)   │ (None, 54, 54,    │      5,120 │ max_pooling2d[0]… │
│                     │ 80)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 54, 54,    │        240 │ conv2d_3[0][0]    │
│ (BatchNormalizatio… │ 80)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_3        │ (None, 54, 54,    │          0 │ batch_normalizat… │
│ (Activation)        │ 80)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_4 (Conv2D)   │ (None, 52, 52,    │    138,240 │ activation_3[0][… │
│                     │ 192)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ batch_normalizatio… │ (None, 52, 52,    │        576 │ conv2d_4[0][0]    │
│ (BatchNormalizatio… │ 192)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ activation_4        │ (None, 52, 52,    │          0 │ batch_normalizat

 Total params: 73,663,490 (281.00 MB)

 Trainable params: 73,602,946 (280.77 MB)

 Non-trainable params: 60,544 (236.50 KB)

#### 3.2 Обучение и сохранение модели Inception-ResNet-v2

In [ ]:
tfb = TensorBoard('object_detection')
history = model.fit(x=x_train,y=y_train,batch_size=10,epochs=180,
                    validation_data=(x_test,y_test),callbacks=[tfb])

Epoch 1/180


d:\Progect\Number_auto\.venv\Lib\site-packages\keras\src\models\functional.py:238: UserWarning:

The structure of `inputs` doesn't match the expected structure.
Expected: ['keras_tensor']
Received: inputs=Tensor(shape=(None, 224, 224, 3))



88/88 ━━━━━━━━━━━━━━━━━━━━ 0s 11s/step - loss: 0.0429 

d:\Progect\Number_auto\.venv\Lib\site-packages\keras\src\models\functional.py:238: UserWarning:

The structure of `inputs` doesn't match the expected structure.
Expected: ['keras_tensor']
Received: inputs=Tensor(shape=(10, 224, 224, 3))



88/88 ━━━━━━━━━━━━━━━━━━━━ 1153s 12s/step - loss: 0.0427 - val_loss: 0.0129
Epoch 2/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1018s 12s/step - loss: 0.0055 - val_loss: 0.0125
Epoch 3/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1011s 11s/step - loss: 0.0041 - val_loss: 0.0092
Epoch 4/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1008s 11s/step - loss: 0.0022 - val_loss: 0.0135
Epoch 5/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1013s 12s/step - loss: 0.0020 - val_loss: 0.0127
Epoch 6/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1067s 12s/step - loss: 0.0017 - val_loss: 0.0132
Epoch 7/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1087s 12s/step - loss: 0.0011 - val_loss: 0.0128
Epoch 8/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1102s 12s/step - loss: 0.0013 - val_loss: 0.0165
Epoch 9/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1040s 12s/step - loss: 0.0011 - val_loss: 0.0156
Epoch 10/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1081s 12s/step - loss: 0.0010 - val_loss: 0.0126
Epoch 11/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 1061s 12s/step - loss: 0.0012 - val_loss: 0.0197
Epoch 12/180
88/88 ━━━━━━━━━━━━━━━━━━━━ 10

In [58]:
model.save('./object_detection.h5')

### 4. Pipeline

#### 4.1 Сделаем прогноз

In [ ]:
# Load model
model = tf.keras.models.load_model('./object_detection.h5')
print('Model loaded Sucessfully')

Далее загружаем нашу картинку TEST с правильным путем к ней. Я загрузил еще несколько изображений только для этой цели - папку TEST.

In [81]:
path = 'D:/Progect/Number_auto/Test/N15.jpeg'
image = load_img(path) # PIL object
image = np.array(image,dtype=np.uint8) # 8 bit array (0,255)
image1 = load_img(path,target_size=(224,224))
image_arr_224 = img_to_array(image1)/255.0  # Convert into array and get the normalized output

# Size of the orginal image
h,w,d = image.shape
print('Height of the image =',h)
print('Width of the image =',w)

Height of the image = 452
Width of the image = 660


Теперь мы можем взглянуть на наше изображение

In [83]:
fig = px.imshow(image)
fig.update_layout(width=700, height=500,  margin=dict(l=10, r=10, b=10, t=10), xaxis_title='Figure 13 - TEST Image')

Посмотрим размер изображения

In [84]:
image_arr_224.shape

(224, 224, 3)

In [85]:
test_arr = image_arr_224.reshape(1,224,224,3)
test_arr.shape

(1, 224, 224, 3)

In [92]:
# Make predictions
coords = model.predict(test_arr)
coords

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 457ms/step


array([[0.37097427, 0.52439654, 0.5944573 , 0.5792892 ]], dtype=float32)

Мы получили выходные данные от модели и выводим то, что мы получили, это нормализованный выход. Итак, нам нужно преобразовать обратно в наши исходные значения формы, что мы и сделали в процессе обучения, в процессе обучения у нас есть исходные значения формы и преобразуем их в нормализованные. Так что по сути мы денормализуем значения обратно.

In [93]:
# Denormalize the values
denorm = np.array([w,w,h,h])
coords = coords * denorm
coords

array([[244.84301984, 346.10171556, 268.6947124 , 261.83871746]])

#### 4.2 Bounting box

Теперь мы нарисуем ограничивающую рамку поверх изображения.

In [94]:
coords = coords.astype(np.int32)
coords

array([[244, 346, 268, 261]], dtype=int32)

In [95]:
# Draw bounding on top the image
xmin, xmax,ymin,ymax = coords[0]
pt1 =(xmin,ymin)
pt2 =(xmax,ymax)
print(pt1, pt2)

(np.int32(244), np.int32(268)) (np.int32(346), np.int32(261))


In [96]:
cv2.rectangle(image,pt1,pt2,(0,255,0),3)
fig = px.imshow(image)
fig.update_layout(width=700, height=500, margin=dict(l=10, r=10, b=10, t=10))

Теперь соберем все это в одном месте и создадим функцию и в конце визуализируем ее. Наш вывод вернет изображение и координаты ограничивающего прямоугольника.

In [ ]:
# Create pipeline
path = 'D:/Progect/Number_auto/TEST/TEST.jpeg'
def object_detection(path):
    
    # Read image
    image = load_img(path) # PIL object
    image = np.array(image,dtype=np.uint8) # 8 bit array (0,255)
    image1 = load_img(path,target_size=(224,224))
    
    # Data preprocessing
    image_arr_224 = img_to_array(image1)/255.0 # Convert to array & normalized
    h,w,d = image.shape
    test_arr = image_arr_224.reshape(1,224,224,3)
    
    # Make predictions
    coords = model.predict(test_arr)
    
    # Denormalize the values
    denorm = np.array([w,w,h,h])
    coords = coords * denorm
    coords = coords.astype(np.int32)
    
    # Draw bounding on top the image
    xmin, xmax,ymin,ymax = coords[0]
    pt1 =(xmin,ymin)
    pt2 =(xmax,ymax)
    print(pt1, pt2)
    cv2.rectangle(image,pt1,pt2,(0,255,0),3)
    return image, coords

image, cods = object_detection(path)

fig = px.imshow(image)
fig.update_layout(width=700, height=500, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='Figure 14')

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 469ms/step
(np.int32(330), np.int32(530)) (np.int32(777), np.int32(508))


### 5. Оптическое распознавание символов

Программное обеспечение для оптического распознавания символов (OCR), которое используется для извлечения текста из изображения.  Я буду использовать EasyOCR. Вы можете найти руководство и файлы для загрузки для установки [здесь](https://github.com/JaidedAI/EasyOCR).

In [109]:
print("Image shape:", img.shape)

Image shape: (719, 960, 3)


In [112]:
print("Coordinates (xmin, xmax, ymin, ymax):", cods[0])

Coordinates (xmin, xmax, ymin, ymax): [346 500 324 351]


#### 5.1 Извлечение текста номерного знака из изображения

Сначала мы загрузим наше изображение и преобразуем его в массив. Обрежем нашу ограничивающую рамку с ее координатами. Мы определим область интереса (ROI) и посмотрим на наше обрезанное изображение 

In [132]:
img = np.array(load_img(path))
xmin ,xmax,ymin,ymax = cods[0]
roi = img[300:350,350:510]
fig = px.imshow(roi)
fig.update_layout(width=350, height=250, margin=dict(l=10, r=10, b=10, t=10),xaxis_title='Figure 15 Cropped image')

In [ ]:
import easyocr
import numpy as np
from PIL import Image

# Инициализация EasyOCR
reader = easyocr.Reader(['en', 'ru'])  # Укажите языки для распознавания (английский и русский)

# Преобразуйте ROI обратно в изображение PIL (необязательно, EasyOCR работает с массивами NumPy)
roi_image = Image.fromarray(roi)

# Распознавание текста из ROI
results = reader.readtext(roi)  # Передаем массив NumPy (roi)

# Вывод распознанного текста
print("Распознанный текст из ROI:")
for (bbox, text, prob) in results:
    print(f"Текст: {text}, Вероятность: {prob:.2f}")

In [ ]:
# extract text from image
text = pt.image_to_string(roi)
print(text)

Очевидно, мы не получили надлежащего текста, но, по крайней мере, вы можете получить 90 процентов информации. И для получения более качественного распознавания текста нам нужно дообучить модель на своих данных. Я это сделаю в следующих примерах. Пока остановимся на на данном шаге.